<h1 align=center><font size = 6><span style="color:blue">Compare the Top 311 Populated Cities in the USA </font></h1>

## <span style="color:blue"> Download all the dependencies that are needed

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

import bs4 as bs
import urllib.request

print('Libraries imported.')

Libraries imported.


## <span style="color:blue">Load in the file using BeautifulSoup 4

#### Tranform the data into a *pandas* dataframe

In [2]:
source = urllib.request.urlopen('https://en.wikipedia.org/wiki/List_of_United_States_cities_by_population').read()
soup = bs.BeautifulSoup(source,'lxml')

In [3]:
tables = soup.find_all("tbody")

In [4]:
i = 1
for table in tables:
    print("# of tables found on the website",i)
    i = i+1
    #print(table)

# of tables found on the website 1
# of tables found on the website 2
# of tables found on the website 3
# of tables found on the website 4
# of tables found on the website 5
# of tables found on the website 6
# of tables found on the website 7
# of tables found on the website 8
# of tables found on the website 9
# of tables found on the website 10
# of tables found on the website 11
# of tables found on the website 12


In [5]:
df = pd.DataFrame()
header_list = []
rows_list = []

for table in tables:
    table_rows = table.find_all('tr')
    #print(table_rows)
    for hd in table_rows:
        th = hd.find_all('th')
        row = [i.text for i in th]
        #print("header",row)
        header_list.append(row)
        #df.append(row)
    for tr in table_rows:
        td = tr.find_all('td')
        row = [i.text for i in td]
        #print(row)
        rows_list.append(row)
        #df.append(row)
    
#print(rows_list)
df = pd.DataFrame(rows_list)
#print(df.head(99))
df.tail(5)

0             1         2                 3           4   \
398  St. Joseph\n    Missouri\n  75,959\n  102,979 (1900)\n   -27,020\n   
399     Trenton\n  New Jersey\n  83,974\n  128,009 (1950)\n   -44,035\n   
400       Utica\n    New York\n  60,100\n  101,740 (1930)\n   -41,640\n   
401  Wilmington\n    Delaware\n  70,635\n  112,504 (1940)\n   -41,869\n   
402  Youngstown\n        Ohio\n  64,958\n  170,002 (1930)\n  -105,044\n   

            5                          6     7     8     9     10  
398  -26.24%\n  6.86% from 1990 to 2010\n  None  None  None  None  
399  -34.40%\n                         \n  None  None  None  None  
400  -40.93%\n  2.61% from 2000 to 2010\n  None  None  None  None  
401  -37.22%\n                         \n  None  None  None  None  
402  -61.79%\n                         \n  None  None  None  None

## <span style="color:blue"> Add the Column Names to the Table

In [6]:
new_data = pd.DataFrame()
new_data1 = pd.DataFrame()
df = df.replace('\n','', regex=True)
new_data = df.dropna(axis = 0, how ='any') 
column_names = ['rank','city', 'state','estimate','census','change','area mi','area km','den mi','den km','location']
new_data1 = pd.DataFrame(new_data.values,columns=column_names)
new_data1 = new_data1.drop(['change','area km','den km'],axis=1) 
new_data1.tail(5)

rank        city    state estimate    census      area mi  \
317     Spring Valley      Nevada  178,395  117,390   +51.97%   86.055 km2   
318          Metairie   Louisiana  138,481  146,136    −5.24%   60.145 km2   
319  East Los Angeles  California  126,496  124,283    +1.78%   19.290 km2   
320        Enterprise      Nevada  108,481   14,676  +639.17%  120.468 km2   
321           Brandon     Florida  103,483   77,895   +32.85%   85.731 km2   

        den mi                                           location  
317  2,073/km2  36°05′55″N 115°15′43″W﻿ / ﻿36.0987°N 115.2619°...  
318  2,302/km2  29°59′52″N 90°10′40″W﻿ / ﻿29.9978°N 90.1779°W﻿...  
319  6,558/km2  34°01′53″N 118°10′07″W﻿ / ﻿34.0315°N 118.1686°...  
320    900/km2  36°01′06″N 115°12′55″W﻿ / ﻿36.0182°N 115.2154°...  
321  1,207/km2  27°56′10″N 82°17′57″W﻿ / ﻿27.9360°N 82.2993°W﻿...

## <span style="color:blue"> Start Cleaning the Data Table

In [7]:
new_data1['lenx'] = new_data1['rank'].apply(len)
new_data1.tail(5)

rank        city    state estimate    census      area mi  \
317     Spring Valley      Nevada  178,395  117,390   +51.97%   86.055 km2   
318          Metairie   Louisiana  138,481  146,136    −5.24%   60.145 km2   
319  East Los Angeles  California  126,496  124,283    +1.78%   19.290 km2   
320        Enterprise      Nevada  108,481   14,676  +639.17%  120.468 km2   
321           Brandon     Florida  103,483   77,895   +32.85%   85.731 km2   

        den mi                                           location  lenx  
317  2,073/km2  36°05′55″N 115°15′43″W﻿ / ﻿36.0987°N 115.2619°...    13  
318  2,302/km2  29°59′52″N 90°10′40″W﻿ / ﻿29.9978°N 90.1779°W﻿...     8  
319  6,558/km2  34°01′53″N 118°10′07″W﻿ / ﻿34.0315°N 118.1686°...    16  
320    900/km2  36°01′06″N 115°12′55″W﻿ / ﻿36.0182°N 115.2154°...    10  
321  1,207/km2  27°56′10″N 82°17′57″W﻿ / ﻿27.9360°N 82.2993°W﻿...     7

In [8]:
new_data1.dtypes

rank        object
city        object
state       object
estimate    object
census      object
area mi     object
den mi      object
location    object
lenx         int64
dtype: object

In [9]:
#new_data1 = new_data[new_data[0] == "1"] 
#new_data1 = pd.DataFrame()

new_data1 = new_data1.loc[new_data1['lenx'] <= 3] 
#iris.ix[iris['sepal length (cm)'] >= 5]
#df[df.name != 'Tina']

#print(new_data.head(10))
new_data1.tail(5)

rank            city        state estimate  census     area mi  \
309  310      Edison[ad]   New Jersey  100,693  99,967  30.1 sq mi   
310  311  Woodbridge[ad]   New Jersey  100,450  99,585  23.3 sq mi   
311  312      San Angelo        Texas  100,215  93,200  59.9 sq mi   
312  313         Kenosha    Wisconsin  100,164  99,218  28.0 sq mi   
313  314       Vacaville   California  100,154  92,428  29.0 sq mi   

          den mi                                           location  lenx  
309  3,389/sq mi  40°30′14″N 74°20′58″W﻿ / ﻿40.5040°N 74.3494°W﻿...     3  
310  4,351/sq mi  40°33′39″N 74°17′34″W﻿ / ﻿40.5607°N 74.2927°W﻿...     3  
311  1,681/sq mi  31°26′28″N 100°27′02″W﻿ / ﻿31.4411°N 100.4505°...     3  
312  3,577/sq mi  42°34′56″N 87°50′44″W﻿ / ﻿42.5822°N 87.8456°W﻿...     3  
313  3,449/sq mi  38°21′14″N 121°58′22″W﻿ / ﻿38.3539°N 121.9728°...     3

In [10]:
#new_data1['lat'] = new_data1['location'].split("/")
new_data1['newloc'] = new_data1['location'].str.split()
#new_data1['lat'] = new_data1[new_data1.newloc[3]]
#new_data1['lat'] = new_data1['newloc'.3]

new_data1.head()

rank              city        state   estimate     census      area mi  \
0    1  New York City[d]     New York  8,398,748  8,175,133  301.5 sq mi   
1    2       Los Angeles   California  3,990,456  3,792,621  468.7 sq mi   
2    3           Chicago     Illinois  2,705,994  2,695,598  227.3 sq mi   
3    4        Houston[3]        Texas  2,325,502  2,100,263  637.5 sq mi   
4    5           Phoenix      Arizona  1,660,272  1,445,632  517.6 sq mi   

         den mi                                           location  lenx  \
0  28,317/sq mi  40°39′49″N 73°56′19″W﻿ / ﻿40.6635°N 73.9387°W﻿...     1   
1   8,484/sq mi  34°01′10″N 118°24′39″W﻿ / ﻿34.0194°N 118.4108°...     1   
2  11,900/sq mi  41°50′15″N 87°40′54″W﻿ / ﻿41.8376°N 87.6818°W﻿...     1   
3   3,613/sq mi  29°47′12″N 95°23′27″W﻿ / ﻿29.7866°N 95.3909°W﻿...     1   
4   3,120/sq mi  33°34′20″N 112°05′24″W﻿ / ﻿33.5722°N 112.0901°...     1   

                                              newloc  
0  [40°39′49″N, 73°56′19″W﻿, /, ﻿40.6635°N, 73.93...  
1  [34°01′10″N, 118°24′39″W﻿, /, ﻿34.0194°N, 118....  
2  [41°50′15″N, 87°40′54″W﻿, /, ﻿41.8376°N, 87.68...  
3  [29°47′12″N, 95°23′27″W﻿, /, ﻿29.7866°N, 95.39...  
4  [33°34′20″N, 112°05′24″W﻿, /, ﻿33.5722°N, 112....

In [11]:
#df2 = pd.DataFrame(df['meta'].str.split().values.tolist())
#df2[['team1','team2']] = pd.DataFrame(df2.teams.values.tolist(), index= df2.index)
#new_data1 = pd.DataFrame(new_data1['location'].str.split().values.tolist())
new_data1[['x0','x1','x2','x3','x4','x5','lat','long','x8','x9','x10','x11']] = pd.DataFrame(new_data1.newloc.values.tolist(), index= new_data1.index)
new_data1 = new_data1.drop(['x0','x1','x2','x3','x4','x5','x8','x9','x10','x11','location','lenx','newloc'],axis=1) 
#new_data1 = new_data1.replace('/','', regex=True)
#new_data1 = new_data1.replace('[d]','', regex=True)
new_data1 = new_data1.replace(';','', regex=True)
new_data1.head()

rank              city        state   estimate     census      area mi  \
0    1  New York City[d]     New York  8,398,748  8,175,133  301.5 sq mi   
1    2       Los Angeles   California  3,990,456  3,792,621  468.7 sq mi   
2    3           Chicago     Illinois  2,705,994  2,695,598  227.3 sq mi   
3    4        Houston[3]        Texas  2,325,502  2,100,263  637.5 sq mi   
4    5           Phoenix      Arizona  1,660,272  1,445,632  517.6 sq mi   

         den mi      lat        long  
0  28,317/sq mi  40.6635   -73.9387﻿  
1   8,484/sq mi  34.0194  -118.4108﻿  
2  11,900/sq mi  41.8376   -87.6818﻿  
3   3,613/sq mi  29.7866   -95.3909﻿  
4   3,120/sq mi  33.5722  -112.0901﻿

In [12]:
new_data1.dtypes

rank        object
city        object
state       object
estimate    object
census      object
area mi     object
den mi      object
lat         object
long        object
dtype: object

In [13]:
new_data1 = new_data1.replace('\ufeff','', regex=True)
new_data1['long'] = new_data1['long'].astype('float64')
new_data1['lat'] = new_data1['lat'].astype('float64')
new_data1.head()

rank              city        state   estimate     census      area mi  \
0    1  New York City[d]     New York  8,398,748  8,175,133  301.5 sq mi   
1    2       Los Angeles   California  3,990,456  3,792,621  468.7 sq mi   
2    3           Chicago     Illinois  2,705,994  2,695,598  227.3 sq mi   
3    4        Houston[3]        Texas  2,325,502  2,100,263  637.5 sq mi   
4    5           Phoenix      Arizona  1,660,272  1,445,632  517.6 sq mi   

         den mi      lat      long  
0  28,317/sq mi  40.6635  -73.9387  
1   8,484/sq mi  34.0194 -118.4108  
2  11,900/sq mi  41.8376  -87.6818  
3   3,613/sq mi  29.7866  -95.3909  
4   3,120/sq mi  33.5722 -112.0901

In [14]:
new_data1.dtypes

rank         object
city         object
state        object
estimate     object
census       object
area mi      object
den mi       object
lat         float64
long        float64
dtype: object

## <span style="color:blue"> Completed Cleaning the Data Table

In [15]:
new_data1.head()

rank              city        state   estimate     census      area mi  \
0    1  New York City[d]     New York  8,398,748  8,175,133  301.5 sq mi   
1    2       Los Angeles   California  3,990,456  3,792,621  468.7 sq mi   
2    3           Chicago     Illinois  2,705,994  2,695,598  227.3 sq mi   
3    4        Houston[3]        Texas  2,325,502  2,100,263  637.5 sq mi   
4    5           Phoenix      Arizona  1,660,272  1,445,632  517.6 sq mi   

         den mi      lat      long  
0  28,317/sq mi  40.6635  -73.9387  
1   8,484/sq mi  34.0194 -118.4108  
2  11,900/sq mi  41.8376  -87.6818  
3   3,613/sq mi  29.7866  -95.3909  
4   3,120/sq mi  33.5722 -112.0901

In [16]:
new_data1.tail()

rank            city        state estimate  census     area mi  \
309  310      Edison[ad]   New Jersey  100,693  99,967  30.1 sq mi   
310  311  Woodbridge[ad]   New Jersey  100,450  99,585  23.3 sq mi   
311  312      San Angelo        Texas  100,215  93,200  59.9 sq mi   
312  313         Kenosha    Wisconsin  100,164  99,218  28.0 sq mi   
313  314       Vacaville   California  100,154  92,428  29.0 sq mi   

          den mi      lat      long  
309  3,389/sq mi  40.5040  -74.3494  
310  4,351/sq mi  40.5607  -74.2927  
311  1,681/sq mi  31.4411 -100.4505  
312  3,577/sq mi  42.5822  -87.8456  
313  3,449/sq mi  38.3539 -121.9728

In [17]:
new_data1.dtypes

rank         object
city         object
state        object
estimate     object
census       object
area mi      object
den mi       object
lat         float64
long        float64
dtype: object

<a id='item1'></a>

## See the shape of the dataframe

In [18]:
new_data1.shape

(314, 9)

## Import Nominatim and Folium

In [19]:
from geopy.geocoders import Nominatim
!conda install -c conda-forge folium=0.5.0
import folium
print("done")

Solving environment: \ 
The environment is inconsistent, please check the package plan carefully
The following packages are causing the inconsistency:

  - defaults/linux-64::anaconda==5.3.1=py37_0
  - defaults/linux-64::astropy==3.0.4=py37h14c3975_0
  - defaults/linux-64::bkcharts==0.2=py37_0
  - defaults/linux-64::blaze==0.11.3=py37_0
  - defaults/linux-64::bokeh==0.13.0=py37_0
  - defaults/linux-64::bottleneck==1.2.1=py37h035aef0_1
  - defaults/linux-64::dask==0.19.1=py37_0
  - defaults/linux-64::datashape==0.5.4=py37_1
  - defaults/linux-64::mkl-service==1.1.2=py37h90e4bf4_5
  - defaults/linux-64::numba==0.39.0=py37h04863e7_0
  - defaults/linux-64::numexpr==2.6.8=py37hd89afb7_0
  - defaults/linux-64::odo==0.5.1=py37_0
  - defaults/linux-64::pytables==3.4.4=py37ha205bf6_0
  - defaults/linux-64::pytest-arraydiff==0.2=py37h39e3cac_0
  - defaults/linux-64::pytest-astropy==0.4.0=py37_0
  - defaults/linux-64::pytest-doctestplus==0.1.3=py37_0
  - defaults/linux-64::pywavelets==1.0.0=py37h

## <span style="color:blue"> Create map with Wichita Kansas as the center of the map

In [20]:
#get geo-graphical date coordinates for Toronto
address = 'Wichita, Kansas'

#geolocator = Nominatim(user_agent="to_explorer")
geolocator = Nominatim(user_agent="torCan_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print("done", address)
print('The geograpical coordinates for {} are {}, {}'.format(address,latitude, longitude))

done Wichita, Kansas
The geograpical coordinates for Wichita, Kansas are 37.6922361, -97.3375448


Now I will loop through the data and fill the dataframe one row at a time

In [21]:
# create map of Toronto using latitude and longitude values
map_USA = folium.Map(location=[latitude, longitude], zoom_start=5)

# add markers to map
for lat, lng, city, estimate, rank in zip(new_data1['lat'], new_data1['long'], new_data1['city'], new_data1['estimate'],new_data1['rank'] ):
    #label = '{}, {}'.format(neighborhood, borough)
    #label = folium.Popup(label, parse_html=True)
    label = 'rank-{}, city-{}, pop-{}'.format(rank, city, estimate)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_USA)
map_USA    

## <span style="color:blue"> Load in the Foursquare Credentails

In [96]:
CLIENT_ID = 'your-client-ID' # your Foursquare ID
CLIENT_SECRET = 'your-client-secret' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

CLIENT_ID = 'KF2QZPIR5QRBSLB2W1BGKLGTIC4PCUGXFHIWS040NIWW' # your Foursquare ID
CLIENT_SECRET = 'PCIZ3IWZEDASC1MMKTUN5GBBA10TGOCJLBQA2IFYSH33' # your Foursquare Secret
VERSION = '20180604'


print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: KF2QZPIR5QRBSLB2W1BGKLGTIC4PCUGXFHIWS040NIWW
CLIENT_SECRET:PCIZ3IWZEDASC1MMKTUN5GBBA10TGOCJLBQA2IFYSH33


In [23]:
new_data1.loc[0, 'city']

'New York City[d]'

In [24]:
neighborhood_latitude = new_data1.loc[0, 'lat'] # neighborhood latitude value
neighborhood_longitude = new_data1.loc[0, 'long'] # neighborhood longitude value

neighborhood_name = new_data1.loc[0, 'city'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of New York City[d] are 40.6635, -73.9387.


In [25]:
# type your answer here

LIMIT = 5 # limit of number of venues returned by Foursquare API

radius = 5000 # define radius

# create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=KF2QZPIR5QRBSLB2W1BGKLGTIC4PCUGXFHIWS040NIWWZOWO&client_secret=PCIZ3IWZEDASC1MMKTUN5GBBA10TGOCJLBQA2IFYSH33THNW&v=20180604&ll=40.6635,-73.9387&radius=5000&limit=5'

In [26]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5ceea2da4434b9213f56fdde'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': '$-$$$$', 'key': 'price'},
    {'name': 'With specials', 'key': 'specials'}]},
  'headerLocation': 'Brooklyn',
  'headerFullLocation': 'Brooklyn',
  'headerLocationGranularity': 'city',
  'totalResults': 239,
  'suggestedBounds': {'ne': {'lat': 40.708500045000044,
    'lng': -73.87948696388868},
   'sw': {'lat': 40.618499954999955, 'lng': -73.99791303611131}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '573f7a57498eec371cec96c2',
       'name': 'Empanada City',
       'location': {'address': '363 Lincoln Rd',
        'crossStreet': 'Nostrand Ave',
        'lat': 40.661631197708445,
        'lng': -73.95043556642821,
   

In [27]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']
print("done")    

done


In [28]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name            categories        lat        lng
0                Empanada City   Empanada Restaurant  40.661631 -73.950436
1              The Food Sermon  Caribbean Restaurant  40.664588 -73.953735
2  PLG Coffee House and Tavern                  Café  40.660007 -73.953362
3                Colina Cuervo                  Café  40.671330 -73.950420
4                         Glou      Tapas Restaurant  40.662949 -73.953869

In [29]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

5 venues were returned by Foursquare.


In [30]:
def getNearbyVenues(names, latitudes, longitudes, radius=1000):
    
    LIMIT = 20
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['city', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)
print("done")

done


## <span style="color:blue"> Explore Cities in the USA
## <span style="color:blue"> Let's create a function to repeat the same process to all the cities in the USA

In [31]:
# type your answer here

city_venues = getNearbyVenues(names=new_data1['city'],
                                   latitudes=new_data1['lat'],
                                   longitudes=new_data1['long']
                                  )
print("done")


New York City[d]
Los Angeles
Chicago
Houston[3]
Phoenix
Philadelphia[e]
San Antonio
San Diego
Dallas
San Jose
Austin
Jacksonville[f]
Fort Worth
Columbus
San Francisco[g]
Charlotte
Indianapolis[h]
Seattle
Denver[i]
Washington, D.C.[j]
Boston
El Paso
Detroit
Nashville[k]
Portland
Memphis
Oklahoma City
Las Vegas
Louisville[l]
Baltimore[m]
Milwaukee
Albuquerque
Tucson
Fresno
Mesa
Sacramento
Atlanta
Kansas City
Colorado Springs
Miami
Raleigh
Omaha
Long Beach
Virginia Beach[m]
Oakland
Minneapolis
Tulsa
Arlington
Tampa
New Orleans[n]
Wichita
Cleveland
Bakersfield
Aurora
Anaheim
Honolulu[b]
Santa Ana
Riverside
Corpus Christi
Lexington[o]
Stockton
Henderson
Saint Paul
St. Louis[m]
Cincinnati
Pittsburgh
Greensboro
Anchorage[p]
Plano
Lincoln
Orlando
Irvine
Newark
Toledo
Durham
Chula Vista
Fort Wayne
Jersey City
St. Petersburg
Laredo
Madison
Chandler
Buffalo
Lubbock
Scottsdale
Reno
Glendale
Gilbert[q]
Winston–Salem
North Las Vegas
Norfolk[m]
Chesapeake[m]
Garland
Irving
Hialeah
Fremont
Boise[r]
Ri

In [34]:
print(city_venues.shape)
city_venues.head(30)

(4941, 7)


city  Neighborhood Latitude  Neighborhood Longitude  \
0   New York City[d]                40.6635                -73.9387   
1   New York City[d]                40.6635                -73.9387   
2   New York City[d]                40.6635                -73.9387   
3   New York City[d]                40.6635                -73.9387   
4   New York City[d]                40.6635                -73.9387   
5   New York City[d]                40.6635                -73.9387   
6   New York City[d]                40.6635                -73.9387   
7   New York City[d]                40.6635                -73.9387   
8   New York City[d]                40.6635                -73.9387   
9   New York City[d]                40.6635                -73.9387   
10  New York City[d]                40.6635                -73.9387   
11  New York City[d]                40.6635                -73.9387   
12  New York City[d]                40.6635                -73.9387   
13  New York City[d]                40.6635                -73.9387   
14  New York City[d]                40.6635                -73.9387   
15  New York City[d]                40.6635                -73.9387   
16  New York City[d]                40.6635                -73.9387   
17  New York City[d]                40.6635                -73.9387   
18  New York City[d]                40.6635                -73.9387   
19  New York City[d]                40.6635                -73.9387   
20       Los Angeles                34.0194               -118.4108   
21       Los Angeles                34.0194               -118.4108   
22       Los Angeles                34.0194               -118.4108   
23       Los Angeles                34.0194               -118.4108   
24       Los Angeles                34.0194               -118.4108   
25       Los Angeles                34.0194               -118.4108   
26       Los Angeles                34.0194               -118.4108   
27       Los Angeles                34.0194               -118.4108   
28       Los Angeles                34.0194               -118.4108   
29       Los Angeles                34.0194               -118.4108   

                                  Venue  Venue Latitude  Venue Longitude  \
0            Izzy's Brooklyn Smokehouse       40.664869       -73.937023   
1                       Ali's Roti Shop       40.666436       -73.931346   
2                     Sweet Expressions       40.668382       -73.942337   
3                                Bodega       40.668388       -73.932366   
4                      The Market Place       40.662153       -73.943010   
5             Mama Louisa's Hero Shoppe       40.659496       -73.947519   
6     Conrad's Famous Bakery, III, Inc.       40.667942       -73.931033   
7                              Calabria       40.670420       -73.942230   
8        Crunch Fitness - Crown Heights       40.663335       -73.932808   
9              Jewish Children's Museum       40.669017       -73.942086   
10                           Sushi Spot       40.664320       -73.942705   
11          Blink Fitness Crown Heights       40.669828       -73.931352   
12       Fish N Chips (Soul of the Sea)       40.661951       -73.940055   
13               Kings County Nurseries       40.659171       -73.947301   
14                  Old Boys High Field       40.658667       -73.938427   
15              Three Star Juice Lounge       40.661465       -73.931672   
16                        Family Dollar       40.662678       -73.933558   
17                         White Castle       40.663357       -73.932238   
18                             Rite Aid       40.661066       -73.931816   
19                              Bakerie       40.672013       -73.939183   
20               Oldfield's Liquor Room       34.016286      -118.411881   
21                           Yogurtland       34.017710      -118.407116   
22             Pampas Grill Culver City       34.016929      -118.

In [35]:
city_venues.groupby('city').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
city                                                                        
Abilene                                 20                      20     20   
Akron                                   20                      20     20   
Albuquerque                             20                      20     20   
Alexandria[m]                           15                      15     15   
Allen                                   20                      20     20   
Allentown                               20                      20     20   
Amarillo                                20                      20     20   
Anaheim                                  9                       9      9   
Ann Arbor                               20                      20     20   
Antioch                                 15                      15     15   
Arlington                               20                      20     20   
Arvada                                  13                      13     13   
Athens[z]                               20                      20     20   
Atlanta                                 13                      13     13   
Augusta[t]                               1                       1      1   
Aurora                                   9                       9      9   
Austin                                  20                      20     20   
Bakersfield                             20                      20     20   
Baltimore[m]                            20                      20     20   
Baton Rouge[s]                          20                      20     20   
Beaumont                                20                      20     20   
Bellevue                                11                      11     11   
Berkeley                                20                      20     20   
Billings                                20                      20     20   
Birmingham                              20                      20     20   
Boise[r]                                13                      13     13   
Boston                                  19                      19     19   
Boulder                                 20                      20     20   
Bridgeport                              20                      20     20   
Broken Arrow                             7                       7      7   
Buffalo                                 20                      20     20   
Burbank                                 20                      20     20   
Cambridge                               20                      20     20   
Cape Coral                              20                      20     20   
Carlsbad                                20                      20     20   
Carrollton                              20                      20     20   
Cary[v]                                 20                      20     20   
Cedar Rapids                            20                      20     20   
Centennial                              20                      20     20   
Chandler                                16                      16     16   
Charleston                              15                      15     15   
Charlotte                               20                      20     20   
Chattanooga                              4                       4      4   
Chicago                                 20                      20     20   
Chula Vista                              6                       6      6   
Cincinnati                              20                      20     20   
Clarksville                              2                       2      2   
Clearwater                               7                       7      7   
Cleveland                               20                      20     20   
Clinton[ae]                              5                       5      5   
Clovis           

In [37]:
print('There are {} uniques categories.'.format(len(city_venues['Venue Category'].unique())))

There are 378 uniques categories.


In [38]:
# one hot encoding
city_onehot = pd.get_dummies(city_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
city_onehot['city'] = city_venues['city'] 

# move neighborhood column to the first column
fixed_columns = [city_onehot.columns[-1]] + list(city_onehot.columns[:-1])
city_onehot = city_onehot[fixed_columns]

city_onehot.head()

city  ATM  Accessories Store  Adult Boutique  \
0  New York City[d]    0                  0               0   
1  New York City[d]    0                  0               0   
2  New York City[d]    0                  0               0   
3  New York City[d]    0                  0               0   
4  New York City[d]    0                  0               0   

   Advertising Agency  Afghan Restaurant  African Restaurant  Airport  \
0                   0                  0                   0        0   
1                   0                  0                   0        0   
2                   0                  0                   0        0   
3                   0                  0                   0        0   
4                   0                  0                   0        0   

   Airport Gate  Airport Service  Airport Terminal  American Restaurant  \
0             0                0                 0                    0   
1             0                0                 0                    0   
2             0                0                 0                    0   
3             0                0                 0                    0   
4             0                0                 0                    0   

   Animal Shelter  Antique Shop  Arcade  Argentinian Restaurant  Art Gallery  \
0               0             0       0                       0            0   
1               0             0       0                       0            0   
2               0             0       0                       0            0   
3               0             0       0                       0            0   
4               0             0       0                       0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Astrologer  \
0           0                    0                 0           0   
1           0                    0                 0           0   
2           0                    0                 0           0   
3           0                    0                 0           0   
4           0                    0                 0           0   

   Athletics & Sports  Austrian Restaurant  Auto Dealership  Auto Garage  \
0                   0                    0                0            0   
1                   0                    0                0            0   
2                   0                    0                0            0   
3                   0                    0                0            0   
4                   0                    0                0            0   

   Auto Workshop  Automotive Shop  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  \
0              0                0          1           0       0     0    0   
1              0                0          0           0       0     0    0   
2              0                0          0           0       0     0    0   
3              0                0          0           0       0     0    0   
4              0                0          0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Basketball Stadium  \
0               0                 0                 0                   0   
1               0                 0                 0                   0   
2               0                 0                 0                   0   
3               0                 0                 0                   0   
4               0                 0                 0                   0   

   Beach  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0      0                0         0            0           0              0   
1      0                0         0            0           0              0   
2      0                0         0            0           0              0   
3      0                0         0            0           0              0   
4      0                0         0            0           0      

In [39]:
city_onehot.shape

(4941, 379)

In [40]:
city_grouped = city_onehot.groupby('city').mean().reset_index()
city_grouped

city       ATM  Accessories Store  Adult Boutique  \
0                Abilene  0.000000           0.000000        0.000000   
1                  Akron  0.000000           0.000000        0.000000   
2            Albuquerque  0.000000           0.000000        0.000000   
3          Alexandria[m]  0.000000           0.000000        0.000000   
4                  Allen  0.000000           0.000000        0.000000   
5              Allentown  0.000000           0.000000        0.000000   
6               Amarillo  0.000000           0.000000        0.000000   
7                Anaheim  0.000000           0.000000        0.000000   
8              Ann Arbor  0.000000           0.000000        0.000000   
9                Antioch  0.000000           0.000000        0.000000   
10             Arlington  0.000000           0.000000        0.000000   
11                Arvada  0.000000           0.000000        0.000000   
12             Athens[z]  0.000000           0.000000        0.000000   
13               Atlanta  0.000000           0.000000        0.000000   
14            Augusta[t]  0.000000           0.000000        0.000000   
15                Aurora  0.000000           0.000000        0.111111   
16                Austin  0.000000           0.000000        0.000000   
17           Bakersfield  0.000000           0.000000        0.000000   
18          Baltimore[m]  0.000000           0.000000        0.000000   
19        Baton Rouge[s]  0.000000           0.000000        0.000000   
20              Beaumont  0.000000           0.000000        0.000000   
21              Bellevue  0.000000           0.000000        0.000000   
22              Berkeley  0.000000           0.000000        0.000000   
23              Billings  0.050000           0.000000        0.000000   
24            Birmingham  0.000000           0.000000        0.000000   
25              Boise[r]  0.000000           0.000000        0.000000   
26                Boston  0.000000           0.000000        0.000000   
27               Boulder  0.000000           0.000000        0.000000   
28            Bridgeport  0.000000           0.000000        0.000000   
29          Broken Arrow  0.000000           0.000000        0.000000   
30               Buffalo  0.000000           0.000000        0.000000   
31               Burbank  0.000000           0.000000        0.000000   
32             Cambridge  0.000000           0.000000        0.000000   
33            Cape Coral  0.000000           0.000000        0.000000   
34              Carlsbad  0.000000           0.000000        0.000000   
35            Carrollton  0.000000           0.000000        0.000000   
36               Cary[v]  0.000000           0.000000        0.000000   
37          Cedar Rapids  0.000000           0.000000        0.000000   
38            Centennial  0.000000           0.000000        0.000000   
39              Chandler  0.000000           0.000000        0.000000   
40            Charleston  0.000000           0.000000        0.000000   
41             Charlotte  0.000000           0.000000        0.000000   
42           Chattanooga  0.000000           0.000000        0.000000   
43               Chicago  0.000000           0.000000        0.000000   
44           Chula Vista  0.000000           0.000000        0.000000   
45            Cincinnati  0.000000           0.000000        0.000000   
46           Clarksville  0.000000           0.000000        0.000000   
47            Clearwater  0.000000           0.000000        0.000000   
48             Cleveland  0.000000           0.000000        0.000000   
49           Clinton[ae]  0.000000           0.000000        0.000000   
50                Clovis  0.050000           0.000000        0.000000   
51       College Station  0.000000           0.000000        0.000000   
52      Colorado Springs  0.000000           0.000000        0.000000   
53              Columbia  0.000000           0.000000        0.000000   
54   

In [41]:
city_grouped.shape

(300, 379)

In [43]:
num_top_venues = 10

for hood in city_grouped['city']:
    print("----"+hood+"----")
    temp = city_grouped[city_grouped['city'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 4})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Abilene----
                    venue  freq
0     American Restaurant  0.20
1       Convention Center  0.05
2             Art Gallery  0.05
3  Furniture / Home Store  0.05
4    Fast Food Restaurant  0.05
5                 Theater  0.05
6             Candy Store  0.05
7                    Park  0.05
8                  Bakery  0.05
9         Automotive Shop  0.05


----Akron----
                      venue  freq
0     Performing Arts Venue  0.10
1            Sandwich Place  0.05
2         Food & Drink Shop  0.05
3                  Boutique  0.05
4                      Café  0.05
5             Souvenir Shop  0.05
6           Thai Restaurant  0.05
7        Mexican Restaurant  0.05
8      Fast Food Restaurant  0.05
9  Mediterranean Restaurant  0.05


----Albuquerque----
                venue  freq
0             Brewery  0.20
1  Mexican Restaurant  0.15
2      Discount Store  0.10
3        Burger Joint  0.05
4      Shipping Store  0.05
5          Truck Stop  0.05
6      Sandwich Place  0

In [86]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [87]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['city']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['city'] = city_grouped['city']

for ind in np.arange(city_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(city_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

city  1st Most Common Venue 2nd Most Common Venue  \
0        Abilene    American Restaurant     Convention Center   
1          Akron  Performing Arts Venue                   Bar   
2    Albuquerque                Brewery    Mexican Restaurant   
3  Alexandria[m]                   Park   Rental Car Location   
4          Allen   Fast Food Restaurant                  Café   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0    Seafood Restaurant                Bakery           Candy Store   
1     Food & Drink Shop                  Café    Italian Restaurant   
2        Discount Store          Burger Joint             Pawn Shop   
3           Coffee Shop           Flower Shop        Ice Cream Shop   
4             BBQ Joint    Mexican Restaurant            Donut Shop   

  6th Most Common Venue   7th Most Common Venue 8th Most Common Venue  \
0       Automotive Shop  Furniture / Home Store                  Park   
1           Coffee Shop              Art Museum  Fast Food Restaurant   
2        Shipping Store              Truck Stop                 Hotel   
3           Gas Station      Chinese Restaurant         Grocery Store   
4        Ice Cream Shop             Coffee Shop        Discount Store   

  9th Most Common Venue 10th Most Common Venue  
0           Coffee Shop              Rock Club  
1       Thai Restaurant            Music Venue  
2        Sandwich Place              Wine Shop  
3           Pizza Place                    Gym  
4  Gym / Fitness Center               Pharmacy

## <span style="color:blue"> Set the Number of Clusters to use

In [88]:
# set number of clusters
kclusters = 5

city_grouped_clustering = city_grouped.drop('city', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(city_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 2, 2, 0, 1, 2, 2, 2, 2, 1], dtype=int32)

In [89]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

city_merged = new_data1

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
city_merged = city_merged.join(neighborhoods_venues_sorted.set_index('city'), on='city')

city_merged.head() # check the last columns!




rank              city        state   estimate     census      area mi  \
0    1  New York City[d]     New York  8,398,748  8,175,133  301.5 sq mi   
1    2       Los Angeles   California  3,990,456  3,792,621  468.7 sq mi   
2    3           Chicago     Illinois  2,705,994  2,695,598  227.3 sq mi   
3    4        Houston[3]        Texas  2,325,502  2,100,263  637.5 sq mi   
4    5           Phoenix      Arizona  1,660,272  1,445,632  517.6 sq mi   

         den mi      lat      long  Cluster Labels 1st Most Common Venue  \
0  28,317/sq mi  40.6635  -73.9387             1.0             BBQ Joint   
1   8,484/sq mi  34.0194 -118.4108             2.0           Pizza Place   
2  11,900/sq mi  41.8376  -87.6818             1.0  Fast Food Restaurant   
3   3,613/sq mi  29.7866  -95.3909             2.0                  Café   
4   3,120/sq mi  33.5722 -112.0901             1.0  Fast Food Restaurant   

       2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0              Grocery Store                 Field  Fast Food Restaurant   
1          Indian Restaurant                  Café  Brazilian Restaurant   
2                      Diner           Coffee Shop      Video Game Store   
3  Cajun / Creole Restaurant    Italian Restaurant            Beer Store   
4           Storage Facility           Video Store              Pharmacy   

      5th Most Common Venue   6th Most Common Venue 7th Most Common Venue  \
0                    Museum                    Café           Candy Store   
1  Mediterranean Restaurant             Coffee Shop         Smoothie Shop   
2              Intersection  Thrift / Vintage Store         Shopping Mall   
3               Coffee Shop            Dessert Shop    Seafood Restaurant   
4            Sandwich Place              Nail Salon             Speakeasy   

   8th Most Common Venue 9th Most Common Venue      10th Most Common Venue  
0          Garden Center  Caribbean Restaurant                      Bakery  
1             Taco Place        Ice Cream Shop          Frozen Yogurt Shop  
2                   Lake    Chinese Restaurant               Train Station  
3  Vietnamese Restaurant   American Restaurant                   Juice Bar  
4    Sporting Goods Shop    Mexican Restaurant  Construction & Landscaping

In [90]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=4)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(city_merged['lat'], city_merged['long'], city_merged['city'], city_merged['Cluster Labels']):
    try:
        cluster1 = int(cluster)
    except:
        cluster1 = int(0)
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster1), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster1-1],
        fill=True,
        fill_color=rainbow[cluster1-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## <span style="color:blue"> Cities from Cluster 1

In [91]:
city_merged.loc[city_merged['Cluster Labels'] == 0, city_merged.columns[[1] + list(range(5, city_merged.shape[1]))]]

city      area mi        den mi      lat      long  \
11    Jacksonville[f]  747.4 sq mi   1,178/sq mi  30.3369  -81.6616   
17            Seattle   83.8 sq mi   8,405/sq mi  47.6205 -122.3509   
18          Denver[i]  153.3 sq mi   4,521/sq mi  39.7619 -104.8811   
20             Boston   48.3 sq mi  13,938/sq mi  42.3320  -71.0202   
21            El Paso  256.8 sq mi   2,660/sq mi  31.8484 -106.4270   
23       Nashville[k]  475.9 sq mi   1,388/sq mi  36.1718  -86.7850   
27          Las Vegas  134.4 sq mi   4,709/sq mi  36.2292 -115.2601   
28      Louisville[l]  263.5 sq mi   2,339/sq mi  38.1654  -85.6474   
36            Atlanta  133.5 sq mi   3,539/sq mi  33.7629  -84.4227   
42         Long Beach   50.3 sq mi   9,347/sq mi  33.8092 -118.1553   
45        Minneapolis   54.0 sq mi   7,660/sq mi  44.9633  -93.2683   
49     New Orleans[n]  169.4 sq mi   2,311/sq mi  30.0534  -89.9345   
53             Aurora  153.5 sq mi   2,356/sq mi  39.6880 -104.6897   
55        Honolulu[b]   60.5 sq mi   5,815/sq mi  21.3243 -157.8476   
60           Stockton   61.7 sq mi   4,977/sq mi  37.9763 -121.3133   
61          Henderson  104.7 sq mi   2,798/sq mi  36.0097 -115.0357   
62         Saint Paul   52.0 sq mi   5,815/sq mi  44.9489  -93.1041   
64         Cincinnati   77.4 sq mi   3,860/sq mi  39.1402  -84.5058   
65         Pittsburgh   55.4 sq mi   5,481/sq mi  40.4398  -79.9766   
70            Orlando  105.2 sq mi   2,635/sq mi  28.4166  -81.2736   
71             Irvine   65.6 sq mi   4,057/sq mi  33.6784 -117.7713   
74             Durham  109.8 sq mi   2,395/sq mi  35.9811  -78.9029   
75        Chula Vista   49.6 sq mi   5,387/sq mi  32.6277 -117.0152   
77        Jersey City   14.8 sq mi  17,848/sq mi  40.7114  -74.0648   
79             Laredo  101.1 sq mi   2,544/sq mi  27.5604  -99.4892   
80            Madison   77.0 sq mi   3,280/sq mi  43.0878  -89.4299   
84         Scottsdale  183.9 sq mi   1,341/sq mi  33.6843 -111.8611   
93             Irving   67.0 sq mi   3,557/sq mi  32.8577  -96.9700   
96           Boise[r]   82.1 sq mi   2,718/sq mi  43.6002 -116.2317   
97        Richmond[m]   59.8 sq mi   3,732/sq mi  37.5314  -77.4760   
105     Santa Clarita   52.8 sq mi   3,446/sq mi  34.4030 -118.5042   
108      Fayetteville  147.7 sq mi   1,386/sq mi  35.0828  -78.9735   
109     Moreno Valley   51.3 sq mi   4,006/sq mi  33.9233 -117.2057   
110         Rochester   35.8 sq mi   5,835/sq mi  43.1699  -77.6169   
112  Huntington Beach   26.9 sq mi   7,459/sq mi  33.6906 -118.0093   
116           Yonkers   18.0 sq mi  11,156/sq mi  40.9459  -73.8674   
117            Aurora   44.9 sq mi   4,479/sq mi  41.7635  -88.2901   
120       Little Rock  118.7 sq mi   1,673/sq mi  34.7254  -92.3586   
122        Augusta[t]  302.5 sq mi     652/sq mi  33.3655  -82.0734   
125       Columbus[u]  216.4 sq mi     913/sq mi  32.5102  -84.8749   
126       Tallahassee  100.4 sq mi   1,901/sq mi  30.4551  -84.2534   
129          McKinney   63.0 sq mi   2,735/sq mi  33.1985  -96.6680   
134         Knoxville   98.5 sq mi   1,891/sq mi  35.9707  -83.9493   
137         Vancouver   46.9 sq mi   3,728/sq mi  45.6349 -122.5957   
140           Ontario   49.9 sq mi   3,471/sq mi  34.0394 -117.6042   
141       Chattanooga  143.1 sq mi   1,241/sq mi  35.0660  -85.2484   
143   Newport News[m]   69.1 sq mi   2,631/sq mi  37.0762  -76.5220   
146         Oceanside   41.3 sq mi   4,249/sq mi  33.2245 -117.3062   
150    Pembroke Pines   33.0 sq mi   5,109/sq mi  26.0210  -80.3404   
157           Jackson  111.0 sq mi   1,524/sq mi  32.3158  -90.2128   
158     Alexandria[m]   15.0 sq mi  10,387/sq mi  38.8201  -77.0841   
166         Hollywood   27.3 sq mi   5,568/sq mi  26.0310  -80.1646   
168         Sunnyvale   22.0 sq mi   6,944/sq mi  37.3858 -122.0263   
170    Kansas City[x]  124.8 sq mi   1,216/sq mi  39.1225  -94.7418   
176          Bellevue   33.5 sq mi   4,221/sq mi  47.5979 -122.1565   
178          Savannah  103.6 sq mi   1,41

## <span style="color:blue"> Cities from Cluster 2

In [92]:
city_merged.loc[city_merged['Cluster Labels'] == 1, city_merged.columns[[1] + list(range(5, city_merged.shape[1]))]]

city      area mi        den mi      lat      long  \
0    New York City[d]  301.5 sq mi  28,317/sq mi  40.6635  -73.9387   
2             Chicago  227.3 sq mi  11,900/sq mi  41.8376  -87.6818   
4             Phoenix  517.6 sq mi   3,120/sq mi  33.5722 -112.0901   
5     Philadelphia[e]  134.2 sq mi  11,683/sq mi  40.0094  -75.1333   
6         San Antonio  461.0 sq mi   3,238/sq mi  29.4724  -98.5251   
8              Dallas  340.9 sq mi   3,866/sq mi  32.7933  -96.7665   
9            San Jose  177.5 sq mi   5,777/sq mi  37.2967 -121.8189   
13           Columbus  218.5 sq mi   3,936/sq mi  39.9852  -82.9848   
22            Detroit  138.8 sq mi   4,847/sq mi  42.3830  -83.1022   
25            Memphis  317.4 sq mi   2,056/sq mi  35.1028  -89.9774   
32             Tucson  230.8 sq mi   2,299/sq mi  32.1531 -110.8706   
38   Colorado Springs  195.6 sq mi   2,378/sq mi  38.8673 -104.7607   
41              Omaha  133.2 sq mi   3,356/sq mi  41.2644  -96.0451   
48              Tampa  113.4 sq mi   3,326/sq mi  27.9701  -82.4797   
52        Bakersfield  148.8 sq mi   2,529/sq mi  35.3212 -119.0183   
56          Santa Ana   27.1 sq mi  12,333/sq mi  33.7363 -117.8830   
57          Riverside   81.2 sq mi   3,999/sq mi  33.9381 -117.3932   
59       Lexington[o]  283.6 sq mi   1,123/sq mi  38.0407  -84.4583   
68              Plano   71.7 sq mi   3,990/sq mi  33.0508  -96.7479   
73             Toledo   80.7 sq mi   3,451/sq mi  41.6641  -83.5819   
81           Chandler   64.9 sq mi   3,813/sq mi  33.2829 -111.8549   
90         Norfolk[m]   53.3 sq mi   4,599/sq mi  36.9230  -76.2446   
92            Garland   57.0 sq mi   4,122/sq mi  32.9098  -96.6303   
98     Baton Rouge[s]   85.9 sq mi   2,651/sq mi  30.4422  -91.1309   
102    San Bernardino   61.5 sq mi   3,516/sq mi  34.1416 -117.2936   
104           Fontana   43.0 sq mi   4,876/sq mi  34.1090 -117.4629   
106        Birmingham  146.1 sq mi   1,452/sq mi  33.5274  -86.7990   
107            Oxnard   26.9 sq mi   7,729/sq mi  34.2023 -119.2046   
113    Salt Lake City  111.2 sq mi   1,742/sq mi  40.7769 -111.9310   
123    Port St. Lucie  118.9 sq mi   1,557/sq mi  27.2806  -80.3883   
124     Grand Prairie   72.3 sq mi   2,637/sq mi  32.6869  -97.0211   
127     Overland Park   75.1 sq mi   2,516/sq mi  38.8890  -94.6906   
132        Shreveport  107.1 sq mi   1,820/sq mi  32.4669  -93.7922   
138   Fort Lauderdale   34.6 sq mi   5,166/sq mi  26.1412  -80.1467   
144  Rancho Cucamonga   40.0 sq mi   4,413/sq mi  34.1233 -117.5642   
147             Salem   48.6 sq mi   3,445/sq mi  44.9237 -123.0232   
151            Peoria  175.7 sq mi     934/sq mi  33.7862 -112.3080   
154           Cary[v]   56.5 sq mi   2,873/sq mi  35.7809  -78.8133   
159           Hayward   45.5 sq mi   3,493/sq mi  37.6287 -122.1024   
161          Lakewood   42.9 sq mi   3,599/sq mi  39.6989 -105.1176   
164           Salinas   23.6 sq mi   6,662/sq mi  36.6902 -121.6337   
169          Macon[w]  249.3 sq mi     612/sq mi  32.8088  -83.6942   
172         Escondido   37.1 sq mi   4,087/sq mi  33.1331 -117.0740   
174        Naperville   38.7 sq mi   3,802/sq mi  41.7492  -88.1620   
177          Rockford   63.5 sq mi   2,325/sq mi  42.2588  -89.0646   
181        Bridgeport   16.1 sq mi   9,064/sq mi  41.1874  -73.1958   
182           McAllen   58.4 sq mi   2,435/sq mi  26.2322  -98.2464   
183          Mesquite   47.2 sq mi   3,045/sq mi  32.7629  -96.5888   
188           Miramar   29.4 sq mi   4,709/sq mi  25.9770  -80.3358   
201            Warren   34.4 sq mi   3,928/sq mi  42.4929  -83.0250   
204           Visalia   37.5 sq mi   3,495/sq mi  36.3273 -119.3289   
208  Sterling Heights   36.5 sq mi   3,628/sq mi  42.5812  -83.0303   
210          Stamford   37.6 sq mi   3,434/sq mi  41.0799  -73.5460   
215        Round Rock   35.6 sq mi   3,396/sq mi  30.5252  -97.6660   
216     Thousand Oaks   55.2 sq mi   2,335/sq mi  34.1933 -118.8742   
217      Lafayette[y]   53.8 sq mi   2,37

## <span style="color:blue"> Cities from Cluster 3

In [93]:
city_merged.loc[city_merged['Cluster Labels'] == 2, city_merged.columns[[1] + list(range(5, city_merged.shape[1]))]]

city      area mi        den mi        lat        long  \
1            Los Angeles  468.7 sq mi   8,484/sq mi  34.019400 -118.410800   
3             Houston[3]  637.5 sq mi   3,613/sq mi  29.786600  -95.390900   
7              San Diego  325.2 sq mi   4,325/sq mi  32.815300 -117.135000   
10                Austin  312.7 sq mi   3,031/sq mi  30.303900  -97.754400   
12            Fort Worth  342.9 sq mi   2,491/sq mi  32.781500  -97.346700   
15             Charlotte  305.4 sq mi   2,757/sq mi  35.207800  -80.831000   
16       Indianapolis[h]  361.5 sq mi   2,366/sq mi  39.776700  -86.145900   
19   Washington, D.C.[j]   61.1 sq mi  11,148/sq mi  38.904100  -77.017200   
24              Portland  133.5 sq mi   4,793/sq mi  45.537000 -122.650000   
26         Oklahoma City  606.3 sq mi   1,053/sq mi  35.467100  -97.513700   
29          Baltimore[m]   80.9 sq mi   7,598/sq mi  39.300000  -76.610500   
30             Milwaukee   96.2 sq mi   6,186/sq mi  43.063300  -87.966700   
31           Albuquerque  188.2 sq mi   2,972/sq mi  35.105600 -106.647400   
33                Fresno  114.4 sq mi   4,563/sq mi  36.783600 -119.793400   
34                  Mesa  137.9 sq mi   3,514/sq mi  33.401900 -111.717400   
35            Sacramento   97.9 sq mi   5,059/sq mi  38.566600 -121.468600   
37           Kansas City  315.0 sq mi   1,528/sq mi  39.125100  -94.551000   
39                 Miami   36.0 sq mi  12,599/sq mi  25.775200  -80.208600   
40               Raleigh  145.1 sq mi   3,163/sq mi  35.830600  -78.641800   
43     Virginia Beach[m]  244.7 sq mi   1,850/sq mi  36.780000  -76.025200   
44               Oakland   55.9 sq mi   7,514/sq mi  37.769800 -122.225700   
46                 Tulsa  196.8 sq mi   2,048/sq mi  36.127900  -95.902300   
47             Arlington   95.8 sq mi   4,100/sq mi  32.700700  -97.124700   
50               Wichita  160.4 sq mi   2,431/sq mi  37.690700  -97.345900   
51             Cleveland   77.7 sq mi   4,965/sq mi  41.478500  -81.679400   
54               Anaheim   50.0 sq mi   7,021/sq mi  33.855500 -117.760100   
63          St. Louis[m]   62.0 sq mi   5,023/sq mi  38.635700  -90.244600   
66            Greensboro  128.3 sq mi   2,237/sq mi  36.095100  -79.827000   
69               Lincoln   92.1 sq mi   3,044/sq mi  40.810500  -96.680300   
72                Newark   24.1 sq mi  11,691/sq mi  40.724200  -74.172600   
76            Fort Wayne  110.6 sq mi   2,391/sq mi  41.088200  -85.143900   
78        St. Petersburg   61.8 sq mi   4,223/sq mi  27.762000  -82.644100   
82               Buffalo   40.4 sq mi   6,359/sq mi  42.892500  -78.859700   
83               Lubbock  124.6 sq mi   2,027/sq mi  33.565600 -101.886700   
85                  Reno  107.3 sq mi   2,286/sq mi  39.549100 -119.849900   
86              Glendale   59.1 sq mi   4,161/sq mi  33.533100 -112.189900   
87            Gilbert[q]   68.0 sq mi   3,487/sq mi  33.310300 -111.743100   
88         Winston–Salem  132.5 sq mi   1,828/sq mi  36.102700  -80.261000   
89       North Las Vegas   98.0 sq mi   2,436/sq mi  36.285700 -115.093900   
94               Hialeah   21.5 sq mi  10,995/sq mi  25.869900  -80.302900   
95               Fremont   77.5 sq mi   3,008/sq mi  37.494500 -121.941200   
99               Spokane   68.7 sq mi   3,144/sq mi  47.666900 -117.433300   
100           Des Moines   88.9 sq mi   2,424/sq mi  41.572600  -93.610200   
101               Tacoma   49.7 sq mi   4,251/sq mi  47.252200 -122.459800   
103              Modesto   43.0 sq mi   4,934/sq mi  37.637500 -121.003000   
111             Glendale   30.4 sq mi   6,606/sq mi  34.181400 -118.245800   
114         Grand Rapids   44.4 sq mi   4,424/sq mi  42.961200  -85.655600   
115             Amarillo  101.4 sq mi   1,968/sq mi  35.199900 -101.830200   
118           Montgomery  159.8 sq mi   1,252/sq mi  32.347200  -86.266100   
119                Akron   62.0 sq mi   3,188/sq mi  41.080500  -81.521400   
121           Huntsville  213.4 sq mi     

## <span style="color:blue"> Cities from Cluster 4

In [94]:
city_merged.loc[city_merged['Cluster Labels'] == 3, city_merged.columns[[1] + list(range(5, city_merged.shape[1]))]]

city     area mi       den mi      lat     long  \
162      Clarksville  98.3 sq mi  1,529/sq mi  36.5664 -87.3452   
267  West Palm Beach  55.1 sq mi  1,963/sq mi  26.7464 -80.1251   

     Cluster Labels 1st Most Common Venue       2nd Most Common Venue  \
162             3.0          Home Service  Construction & Landscaping   
267             3.0          Home Service          Falafel Restaurant   

    3rd Most Common Venue        4th Most Common Venue 5th Most Common Venue  \
162            Hobby Shop                      Factory           Dry Cleaner   
267   Dumpling Restaurant  Eastern European Restaurant     Electronics Store   

    6th Most Common Venue        7th Most Common Venue 8th Most Common Venue  \
162   Dumpling Restaurant  Eastern European Restaurant     Electronics Store   
267  Ethiopian Restaurant                  Event Space               Exhibit   

    9th Most Common Venue 10th Most Common Venue  
162  Ethiopian Restaurant            Event Space  
267            Eye Doctor            Fabric Shop

## <span style="color:blue"> Cities from Cluster 5

In [95]:
city_merged.loc[city_merged['Cluster Labels'] == 4, city_merged.columns[[1] + list(range(5, city_merged.shape[1]))]]

city      area mi       den mi     lat      long  Cluster Labels  \
163  Palmdale  106.0 sq mi  1,484/sq mi  34.591 -118.1054             4.0   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
163         Deli / Bodega           Zoo Exhibit    Falafel Restaurant   

    4th Most Common Venue        5th Most Common Venue 6th Most Common Venue  \
163   Dumpling Restaurant  Eastern European Restaurant     Electronics Store   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
163  Ethiopian Restaurant           Event Space               Exhibit   

    10th Most Common Venue  
163             Eye Doctor